# Example optimization results 

This notebook demonstrates how to: 
- Get the results of the best optimization trial 
- Visualize optimization results 

In [1]:
import os
import sys

sys.path.insert(0, os.path.abspath("/Users/jmissik/Desktop/repos/fetch3_nhl/"))

In [2]:
from pathlib import Path

from ax.utils.notebook.plotting import render, init_notebook_plotting
from ax.plot.contour import interact_contour
from ax.plot.trace import optimization_trace_single_method
from ax.plot.slice import plot_slice
from ax.service.utils.report_utils import get_standard_plots, exp_to_df
from ax.modelbridge.cross_validation import cross_validate
from ax.plot.contour import interact_contour, plot_contour
from ax.plot.diagnostic import interact_cross_validation, tile_cross_validation
from ax.plot.scatter import(
    interact_fitted,
    plot_objective_vs_constraints,
    tile_fitted,
    plot_multiple_metrics
)
from ax.plot.slice import plot_slice
import numpy as np
from boa import load_experiment_config, scheduler_from_json_file
import plotly.graph_objects as go
import yaml

from fetch3.optimize.fetch_wrapper import get_model_sapflux, get_model_plot_trans

init_notebook_plotting()

[INFO 06-20 02:32:46] ax.utils.notebook.plotting: Injecting Plotly library into cell. Do not overwrite or delete cell.


## Load experiment data

Load the experiment data. Make sure to use the correct paths for your experiment. 

In [3]:
# Full filepath to the scheduler.json file in the experiment output directory
scheduler_fp = Path("/Users/jmissik/Desktop/repos/fetch3_nhl/output/multispecies_UMBS_20220619T214304/scheduler.json")
experiment_dir = scheduler_fp.parent

In [4]:
# CHANGE TO THE CORRECT PATH FOR YOUR CONFIG FILE 
ex_config_file = experiment_dir / "opt_config_ms.yml"
sf_file = Path("/Users/jmissik/Desktop/repos/fetch3_nhl/data/umbs_aggregated_sp_sapflow.csv")
et_file = Path("/Users/jmissik/Desktop/repos/fetch3_nhl/data/partitioned_umbs_et.csv")

Loading the experiment data saved in the scheduler.json file

In [5]:
scheduler = scheduler_from_json_file(scheduler_fp)
experiment = scheduler.experiment
model = scheduler.generation_strategy.model

In [6]:
model.metric_names

{'aspen_sapflux',
 'maple_sapflux',
 'oak_sapflux',
 'pine_sapflux',
 'plot_transpiration'}

## View experiment data

Get the index of the best trial from the experiment

In [7]:
best_trial, best_params, obj = scheduler.get_best_trial(use_model_predictions=False)
best_trial

17

In [8]:
best_params

{'maple_kmax': 7.684332063724493e-05,
 'maple_ap': 1.7344582545773386e-06,
 'maple_bp': -10814302.04865403,
 'maple_p': 15,
 'maple_sat_xylem': 0.6886654360709794,
 'maple_Vcmax25': 48.599421349529116,
 'maple_alpha_gs': 6.501895465604518,
 'maple_wp_s50': -1902576.099174846,
 'maple_c3': 13.462948112383287,
 'oak_kmax': 2.9578078824604034e-06,
 'oak_ap': 8.855992221282268e-06,
 'oak_bp': -7650686.697197619,
 'oak_p': 28,
 'oak_sat_xylem': 0.4313124891872008,
 'oak_Vcmax25': 77.3203247759696,
 'oak_alpha_gs': 5.455874802520023,
 'oak_wp_s50': -1172271.562483448,
 'oak_c3': 20.0,
 'aspen_kmax': 1.8820897560763198e-06,
 'aspen_ap': 5.040220596706172e-06,
 'aspen_bp': -11601422.492124531,
 'aspen_p': 15,
 'aspen_sat_xylem': 0.637358604500601,
 'aspen_Vcmax25': 27.882253153848986,
 'aspen_alpha_gs': 4.0,
 'aspen_wp_s50': -1924621.3020933913,
 'aspen_c3': 9.310843613660072,
 'pine_kmax': 9.44781541146274e-05,
 'pine_ap': 9.241866758355297e-06,
 'pine_bp': -9654334.664692108,
 'pine_p': 29,


Get a dataframe with the experiment data (objective function value, parameter values, 
generation strategy).

Note that generation method is in the last column of the dataframe

In [9]:
results = exp_to_df(experiment)

In [10]:
results

aspen_sapflux  maple_sapflux  oak_sapflux  pine_sapflux  \
0        1.588219       1.084957     3.347931      0.837072   
3        0.979425       0.468434     4.316208      0.763803   
12       1.115849       1.082949     3.348341      0.876871   
13       2.954855       0.846090     7.777635      0.904615   
14       0.953725       1.060090     4.793191      0.875356   
15       0.884041       0.652210     4.134706      0.912687   
16       2.521026       0.856951     7.796769      0.904924   
17       3.574111       0.985644     5.117003      0.889839   
18       3.079583       0.836237     7.674607      0.904321   
19       1.037196       0.704696     9.565001      0.915832   
1        3.854875       0.968256     5.406241      0.888171   
2        2.394286       0.847482     7.954312      0.902736   
4        3.001935       0.835057     7.528928      0.906065   
5        2.987431       0.822420     7.202013      0.907098   
6        3.069142       0.835540     7.431840      0.904850   
7        3.002010       0.838112     7.910068      0.904576   
8        3.676873       0.972800     5.514217      0.888250   
9        2.822251       0.834705     8.473910      0.903806   
10       3.047883       0.836280     6.847652      0.903150   
11       1.004876       0.689854     4.835269      0.879399   

    plot_transpiration  trial_index arm_name  maple_kmax      maple_ap  \
0             5.632883            0      0_0    0.000038  5.381338e-06   
3             3.561779            1      1_0    0.000020  2.678405e-06   
12            3.022368            2      2_0    0.000081  8.098781e-06   
13           14.532932            3      3_0    0.000077  2.098524e-06   
14            4.836503            4      4_0    0.000002  7.191076e-06   
15            2.952619            5      5_0    0.000097  4.811531e-06   
16           13.023448            6      6_0    0.000076  2.120466e-06   
17           12.029094            7      7_0    0.000057  8.265928e-06   
18           14.868982            8      8_0    0.000078  2.075944e-06   
19            8.626612            9      9_0    0.000043  3.621496e-06   
1            13.249882           10     10_0    0.000063  7.199881e-06   
2            12.796702           11     11_0    0.000076  3.200884e-06   
4            14.517877           12     12_0    0.000079  9.356709e-07   
5            14.150467           13     13_0    0.000082  2.834100e-06   
6            14.754737           14     14_0    0.000078  1.764009e-06   
7            14.721221           15     15_0    0.000078  1.791707e-06   
8            12.853150           16     16_0    0.000061  7.428076e-06   
9            14.489678           17     17_0    0.000077  1.734458e-06   
10           13.833945           18     18_0    0.000077  1.728261e-06   
11            3.890949           19     19_0    0.000098  3.717229e-07   

        maple_bp  ...  alpha_2  theta_S2  theta_R2  n_2    Ksat_2  \
0  -1.279637e+07  ...     14.5      0.47     0.045  2.4  0.000034   
3  -9.091019e+06  ...     14.5      0.47     0.045  2.4  0.000034   
12 -9.118189e+06  ...     14.5      0.47     0.045  2.4  0.000034   
13 -1.080542e+07  ...     14.5      0.47     0.045  2.4  0.000034   
14 -4.506498e+06  ...     14.5      0.47     0.045  2.4  0.000034   
15 -1.421641e+07  ...     14.5      0.47     0.045  2.4  0.000034   
16 -1.062677e+07  ...     14.5      0.47     0.045  2.4  0.000034   
17 -8.749794e+06  ...     14.5      0.47     0.045  2.4  0.000034   
18 -1.096902e+07  ...     14.5      0.47     0.045  2.4  0.000034   
19 -1.239318e+07  ...     14.5      0.47     0.045  2.4  0.000034   
1  -9.549909e+06  ...     14.5      0.47     0.045  2.4  0.000034   
2  -1.071481e+07  ...     14.5      0.47     0.045  2.4  0.000034   
4  -1.104813e+07  ...     14.5      0.47     0.045  2.4  0.000034   
5  -1.138521e+07  ...     14.5      0.47     0.045  2.4  0.000034   
6  -1.088681e+07  ...     14.5      0.47     0.045  2.4  0.000034   
7  -1.101716e+07  ...

## Plotting 

### Plot optimization results

In [11]:
render(plot_contour(model=model, param_x='pine_sat_xylem', param_y='oak_sat_xylem', metric_name='maple_sapflux'))

/Users/jmissik/anaconda3/envs/fetch3-dev/lib/python3.9/site-packages/gpytorch/lazy/lazy_tensor.py:1741: UserWarning:

torch.triangular_solve is deprecated in favor of torch.linalg.solve_triangularand will be removed in a future PyTorch release.
torch.linalg.solve_triangular has its arguments reversed and does not return a copy of one of the inputs.
X = torch.triangular_solve(B, A).solution
should be replaced with
X = torch.linalg.solve_triangular(A, B). (Triggered internally at  /Users/distiller/project/conda/conda-bld/pytorch_1646756029501/work/aten/src/ATen/native/BatchLinearAlgebra.cpp:1672.)



In [12]:
cv_results = cross_validate(model)
render(interact_cross_validation(cv_results))

In [13]:
render(optimization_trace_single_method)

AttributeError: 'function' object has no attribute 'plot_type'

In [14]:
METRIC_X_AXIS = 'oak_sapflux'
METRIC_Y_AXIS = 'maple_sapflux'

render(plot_multiple_metrics(
    model,
    metric_x=METRIC_X_AXIS,
    metric_y=METRIC_Y_AXIS,
    rel=False
))

In [15]:
from ax.plot.trace import optimization_trace_single_method

In [16]:
data = scheduler.experiment.fetch_data()

In [17]:

metric_name = 'plot_transpiration'
y = np.array([data.df[data.df["metric_name"] == metric_name]["mean"]])
optimization_direction=(
    (
        "minimize"
        if experiment.metrics[metric_name].lower_is_better is True
        else "maximize"
    )
    if experiment.metrics[metric_name].lower_is_better is not None
    else (
        "minimize" if optimization_config.objective.minimize else "maximize"
    )
)
render(optimization_trace_single_method(y, optimization_direction="minimize", plot_trial_points=True))

NameError: name 'optimization_config' is not defined

In [18]:

# metric_name = 'maple_sapflux'
metric_name = 'plot_transpiration'
y = np.array([data.df[data.df["metric_name"] == metric_name]["mean"]])
optimization_direction=(
    (
        "minimize"
        if experiment.metrics[metric_name].lower_is_better is True
        else "maximize"
    )
    if experiment.metrics[metric_name].lower_is_better is not None
    else (
        "minimize" if optimization_config.objective.minimize else "maximize"
    )
)
render(optimization_trace_single_method(y, optimization_direction="minimize", plot_trial_points=True))

NameError: name 'optimization_config' is not defined

In [19]:
from ax.plot.feature_importances import plot_feature_importance_by_feature_plotly
model = scheduler.generation_strategy.model
plot_feature_importance_by_feature_plotly(model)

### Plot model output vs observations for the best trial in the experiment 

In [79]:
from ax.plot.feature_importances import plot_feature_importance_by_metric_plotly
model = scheduler.generation_strategy.model
plot_feature_importance_by_metric_plotly(model)

In [86]:
from ax.plot.feature_importances import plot_relative_feature_importance_plotly
plot_relative_feature_importance_plotly(model)

In [89]:
from ax.plot.marginal_effects import plot_marginal_effects
render(plot_marginal_effects(model, metric='plot_transpiration'))

/Users/jmissik/anaconda3/envs/fetch3-dev/lib/python3.9/site-packages/ax/plot/marginal_effects.py:39: FutureWarning:

In a future version of pandas all arguments of concat except for the argument 'objs' will be keyword-only.



In [92]:
from ax.plot.scatter import interact_fitted_plotly
interact_fitted_plotly(model, rel=False)

In [20]:
from ax.plot.scatter import lattice_multiple_metrics
render(lattice_multiple_metrics(model, rel=False))

In [21]:
from ax.plot.scatter import plot_objective_vs_constraints
render(plot_objective_vs_constraints(model, objective='plot_transpiration', rel=False))

In [22]:
from ax.plot.scatter import tile_fitted
render(tile_fitted(model, rel=False))

In [23]:
from ax.plot.scatter import tile_observations
render(tile_observations(experiment, rel=False))

In [24]:
from ax.plot.slice import interact_slice_plotly
interact_slice_plotly(model)

In [25]:
experiment.fetch_data().df

arm_name         metric_name      mean  sem  trial_index
0       0_0  plot_transpiration  5.632883  0.0            0
1       0_0       maple_sapflux  1.084957  0.0            0
2       0_0         oak_sapflux  3.347931  0.0            0
3       0_0       aspen_sapflux  1.588219  0.0            0
4       0_0        pine_sapflux  0.837072  0.0            0
..      ...                 ...       ...  ...          ...
95     19_0  plot_transpiration  3.890949  0.0           19
96     19_0       maple_sapflux  0.689854  0.0           19
97     19_0         oak_sapflux  4.835269  0.0           19
98     19_0       aspen_sapflux  1.004876  0.0           19
99     19_0        pine_sapflux  0.879399  0.0           19

[100 rows x 5 columns]

In [26]:
from ax.plot.table_view import table_view_plot
table_view_plot(experiment, experiment.fetch_data(), only_data_frame=True)[0]

0_0       1_0       2_0        3_0       4_0  \
plot_transpiration  5.632883  3.561779  3.022368  14.532932  4.836503   
oak_sapflux         3.347931  4.316208  3.348341   7.777635  4.793191   
maple_sapflux       1.084957  0.468434  1.082949   0.846090  1.060090   
aspen_sapflux       1.588219  0.979425  1.115849   2.954855  0.953725   
pine_sapflux        0.837072  0.763803  0.876871   0.904615  0.875356   

                         5_0        6_0        7_0        8_0       9_0  \
plot_transpiration  2.952619  13.023448  12.029094  14.868982  8.626612   
oak_sapflux         4.134706   7.796769   5.117003   7.674607  9.565001   
maple_sapflux       0.652210   0.856951   0.985644   0.836237  0.704696   
aspen_sapflux       0.884041   2.521026   3.574111   3.079583  1.037196   
pine_sapflux        0.912687   0.904924   0.889839   0.904321  0.915832   

                         10_0       11_0       12_0       13_0       14_0  \
plot_transpiration  13.249882  12.796702  14.517877  14.150467  14.754737   
oak_sapflux          5.406241   7.954312   7.528928   7.202013   7.431840   
maple_sapflux        0.968256   0.847482   0.835057   0.822420   0.835540   
aspen_sapflux        3.854875   2.394286   3.001935   2.987431   3.069142   
pine_sapflux         0.888171   0.902736   0.906065   0.907098   0.904850   

                         15_0       16_0       17_0       18_0      19_0  
plot_transpiration  14.721221  12.853150  14.489678  13.833945  3.890949  
oak_sapflux          7.910068   5.514217   8.473910   6.847652  4.835269  
maple_sapflux        0.838112   0.972800   0.834705   0.836280  0.689854  
aspen_sapflux        3.002010   3.676873   2.822251   3.047883  1.004876  
pine_sapflux         0.904576   0.888250   0.903806   0.903150  0.879399

In [27]:
from ax.plot.trace import get_running_trials_per_minute
render(get_running_trials_per_minute(experiment))

In [28]:
dir_best_trial = (experiment_dir / str(best_trial).zfill(6))
model_file = dir_best_trial / "ds_sapflux.nc"

config_file = dir_best_trial / "config.yml"
with open(config_file, "r") as yml_config:
    model_cfg = yaml.safe_load(yml_config)

config = load_experiment_config(ex_config_file)

In [29]:
objective_funcs = config['optimization_options']['scalarized_objective_options']['objectives']

In [30]:
objective_funcs[0]

{'sklearn_metric': 'mean_absolute_percentage_error',
 'name': 'plot_transpiration',
 'properties': {'obs_file': './data/partitioned_umbs_et.csv',
  'obs_var': 'transpiration_mod',
  'output_var': 'plot_tot',
  'fetch_data_func': 'get_model_plot_trans'}}

In [31]:
ex_settings = config["optimization_options"]
model_settings = config["model_options"]

In [32]:
from fetch3.optimize.fetch_wrapper import get_model_sapflux, get_model_plot_trans

In [33]:
fetch_data_funcs = {get_model_sapflux.__name__: get_model_sapflux,
                    get_model_plot_trans.__name__: get_model_plot_trans}

In [34]:
for obj in objective_funcs:
    
    fetch_data_func = fetch_data_funcs[obj['properties']["fetch_data_func"]]
            
    model, obs = fetch_data_func(
            model_file,
            **obj['properties']
        )
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=obs.index, y=model, name=obj['name']))
    fig.add_trace(go.Scatter(x = obs.index, y=obs, name='observations'))
#     fig.update_layout(yaxis_title = "sap flux [cm3 hr-1]")
    fig.show()